# Facebook Prophet

In [9]:
from fbprophet import Prophet
import warnings
import pandas as pd
import altair as alt
warnings.filterwarnings('ignore')

In [17]:
df = pd.read_csv('test_detect_anoms.csv', names=['ds','y'], skiprows=1)

In [18]:
df

ds        y
0      2018-09-25 14:01:00  182.478
1      2018-09-25 14:02:00  176.231
2      2018-09-25 14:03:00  183.917
3      2018-09-25 14:04:00  177.798
4      2018-09-25 14:05:00  165.469
...                    ...      ...
14393  2018-10-05 13:54:00  151.492
14394  2018-10-05 13:55:00  151.724
14395  2018-10-05 13:56:00  153.776
14396  2018-10-05 13:57:00  150.481
14397  2018-10-05 13:58:00  146.638

[14398 rows x 2 columns]

In [19]:
def fit_predict_model(dataframe, interval_width = 0.99, changepoint_range = 0.8):
    m = Prophet(daily_seasonality = False, yearly_seasonality = False, weekly_seasonality = False,
                seasonality_mode = 'multiplicative', 
                interval_width = interval_width,
                changepoint_range = changepoint_range)
    m = m.fit(dataframe)
    forecast = m.predict(dataframe)
    forecast['fact'] = dataframe['y'].reset_index(drop = True)
    return forecast
    
pred = fit_predict_model(df)

INFO:numexpr.utils:NumExpr defaulting to 8 threads.


In [20]:
def detect_anomalies(forecast):
    forecasted = forecast[['ds','trend', 'yhat', 'yhat_lower', 'yhat_upper', 'fact']].copy()
    #forecast['fact'] = df['y']

    forecasted['anomaly'] = 0
    forecasted.loc[forecasted['fact'] > forecasted['yhat_upper'], 'anomaly'] = 1
    forecasted.loc[forecasted['fact'] < forecasted['yhat_lower'], 'anomaly'] = -1

    #anomaly importances
    forecasted['importance'] = 0
    forecasted.loc[forecasted['anomaly'] ==1, 'importance'] = \
        (forecasted['fact'] - forecasted['yhat_upper'])/forecast['fact']
    forecasted.loc[forecasted['anomaly'] ==-1, 'importance'] = \
        (forecasted['yhat_lower'] - forecasted['fact'])/forecast['fact']
    
    return forecasted

pred = detect_anomalies(pred)

In [21]:
def plot_anomalies(forecasted):
    interval = alt.Chart(forecasted).mark_area(interpolate="basis", color = '#7FC97F').encode(
        x=alt.X('ds:T',  title ='date'),
        y='yhat_upper',
        y2='yhat_lower',
        tooltip=['ds', 'fact', 'yhat_lower', 'yhat_upper']
    ).interactive().properties(
        title='Anomaly Detection'
    )

    fact = alt.Chart(forecasted[forecasted.anomaly==0]).mark_circle(size=15, opacity=0.7, color = 'Black').encode(
        x='ds:T',
        y=alt.Y('fact', title='sales'),    
        tooltip=['ds', 'fact', 'yhat_lower', 'yhat_upper']
    ).interactive()

    anomalies = alt.Chart(forecasted[forecasted.anomaly!=0]).mark_circle(size=30, color = 'Red').encode(
        x='ds:T',
        y=alt.Y('fact', title='sales'),    
        tooltip=['ds', 'fact', 'yhat_lower', 'yhat_upper'],
        size = alt.Size( 'importance', legend=None)
    ).interactive()

    return alt.layer(interval, fact, anomalies)\
              .properties(width=870, height=450)\
              .configure_title(fontSize=20)
              
    plot_anomalies(pred)

In [24]:
plot_anomalies(pred.iloc[:5000])

alt.LayerChart(...)

In [26]:
plot_anomalies(pred.iloc[5001:10000])

alt.LayerChart(...)

In [27]:
plot_anomalies(pred.iloc[10001:])

alt.LayerChart(...)